# Задание 3
1. Изучить на скрытые темы “Преступление и наказание” Реализовать тематическое моделирование через кластеризацию и BERTopic
2. Сравнить эффективность  использования евклидова расстояния и 2 других типов расстояния в кластеризации
3. Визуализировать кластера по выделенным топикам
4. Выложить на github

## Предобработка текста

In [1]:
!gdown 1swDS6kMKlU1EJ5VlxkDeNENnHjNSw5Zi
!pip install bertopic
!pip install umap-learn
!pip install hdbscan
!pip install bertopic
!pip install sentence-transformers
!pip install pymystem3
import nltk
nltk.download('stopwords')

Downloading...
From: https://drive.google.com/uc?id=1swDS6kMKlU1EJ5VlxkDeNENnHjNSw5Zi
To: /content/Crime And Punishment.txt
100% 1.93M/1.93M [00:00<00:00, 13.5MB/s]


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [2]:
import re
import pandas as pd
articles = []
chapters = []
with open('Crime And Punishment.txt', "r") as file:
    chapters = "".join("".join(file.readlines()).split("* * *")[2:])
    chapters = re.split(r'(\r\n|\r|\n)+[MDCLXVI]+(\r\n|\r|\n)', string=chapters, flags=re.IGNORECASE)
    chapters = [chapter for chapter in chapters if len(chapter) > 25]
    articles = [article for chapter in chapters for article in chapter.split("\n") if len(article) > 20]
    sentences = [sentence for article in articles for sentence in article.split(". ") if len(sentence) > 5]

    chapters, articles, sentences = pd.DataFrame({"text": chapters}), pd.DataFrame({"text": articles}), pd.DataFrame({"text": sentences})

print(len(chapters))
print(len(articles))
print(len(sentences))

41
3528
9516


In [3]:
from pymystem3 import Mystem
import string
import nltk
from nltk.corpus import stopwords
def standartize_text(df):
    m = Mystem()
    sw= stopwords.words("russian") + stopwords.words("english")

    df = df.replace(to_replace=r'[^\w\s]', value=" ", regex=True)
    df = df.replace(to_replace=r"(.)\1\1+", value=r'\1\1', regex=True)
    list_patterns = [r'/\w+[^а-я]+\w/iu', r'[string.punctuation]', '/\r?\n|\r/', '\n']
    pattern = re.compile("|".join(list_patterns))
    df = df.replace(to_replace=pattern, value='', regex=True)

    df = df.apply(lambda x: " ".join([word for word in m.lemmatize(x) if word not in sw]))
    df = df.str.strip()
    return df

chapters['text'] = standartize_text(chapters['text'])
articles['text'] = standartize_text(articles['text'])
sentences['text'] = standartize_text(sentences['text'])


In [4]:
sentences = sentences[~sentences['text'].apply(lambda x: "Mädhe" in x)].drop_duplicates().dropna()
sentences.reset_index(inplace=True)

## Выберем на данных какого вида будем обучать BERTtopic

In [ ]:
from bertopic import BERTopic
from nltk.corpus import stopwords
from umap import UMAP
from hdbscan import HDBSCAN
from bertopic import BERTopic
from sentence_transformers import SentenceTransformer
from sklearn.feature_extraction.text import CountVectorizer
from transformers.pipelines import pipeline
from bertopic.representation import KeyBERTInspired
from bertopic.vectorizers import ClassTfidfTransformer

from sentence_transformers import SentenceTransformer

import torch

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
embedding_model = SentenceTransformer('ai-forever/sbert_large_mt_nlu_ru')
umap_model = UMAP(n_components=5, n_neighbors=15, min_dist=0.0)
hdbscan_model = HDBSCAN(min_samples=10, gen_min_span_tree=True, prediction_data=True)
vectorizer_model = CountVectorizer(stop_words=stopwords.words('russian') + stopwords.words('english'))
ctfidf_model = ClassTfidfTransformer()
representation_model = KeyBERTInspired()
def create_topic_model(docs):
    return BERTopic(language="russian", embedding_model=embedding_model, umap_model=umap_model, hdbscan_model=hdbscan_model, vectorizer_model=vectorizer_model, ctfidf_model=ctfidf_model, representation_model=representation_model).fit(docs)


### Деление на главы

Как видим деление на главы не имеет смысла, т.к. модель не может выделить темы для такого маленького обьема данных. Да и у нас есть ограничесние на 512 токенов, так что большая часть главы обрезается

In [ ]:
chapter_model = create_topic_model(chapters['text'].to_list())
chapter_model.get_topic_info()

Topic  Count                                     Name  \
0     -1     41  -1_тотчас_случай_понимать_проговаривать   

                                      Representation  \
0  [тотчас, случай, понимать, проговаривать, дава...   

                                 Representative_Docs  
0  [раскольников   пойти   вслед         это     ...

### Деление на абзацы

Здесь ситуация примерно такая же

In [ ]:
article_model = create_topic_model(articles['text'].to_list())
article_model.get_topic_info()

Topic  Count                                    Name  \
0      0   3511  0_тотчас_случай_понимать_проговаривать   
1      1     17                     1_mädhe_le_dme_mlbh   

                                      Representation  \
0  [тотчас, случай, понимать, проговаривать, дава...   
1  [mädhe, le, dme, mlbh, wll, mée, ee, meh, höe,...   

                                 Representative_Docs  
0  [видеть      верить      думать            шут...  
1  [Mädhe    w   wll     meh    74, полдневный   ...

Error: Runtime no longer has a reference to this dataframe, please re-run this cell and try again.
Error: Runtime no longer has a reference to this dataframe, please re-run this cell and try again.
Error: Runtime no longer has a reference to this dataframe, please re-run this cell and try again.
Error: Runtime no longer has a reference to this dataframe, please re-run this cell and try again.
Error: Runtime no longer has a reference to this dataframe, please re-run this cell and try again.
Error: Runtime no longer has a reference to this dataframe, please re-run this cell and try again.
Error: Runtime no longer has a reference to this dataframe, please re-run this cell and try again.
Error: Runtime no longer has a reference to this dataframe, please re-run this cell and try again.
Error: Runtime no longer has a reference to this dataframe, please re-run this cell and try again.
Error: Runtime no longer has a reference to this dataframe, please re-run this cell and try again.
Error: Run

### Деление на предложения

In [ ]:
sentence_model = create_topic_model(sentences['text'].to_list())
sentence_model.get_topic_info()

Topic  Count                                               Name  \
0       -1   5466                 -1_тотчас_случай_входить_разумихин   
1        0    487         0_раскольников_раскольник_юродивый_николай   
2        1    170                           1_соня_сон_сонечка_спать   
3        2     73          2_одеваться_застегиваться_платье_надевать   
4        3     69          3_отворять_отпирать_отворяться_запираться   
..     ...    ...                                                ...   
157    156      5              156_звякнуть_звонить_стучать_крикнуть   
158    157      5  157_благословлять_уведомлять_посвататься_испол...   
159    158      5      158_выражение_противоречить_лесть_приторность   
160    159      5  159_проговаривать_вздрагивать_свидригайлов_рас...   
161    160      5  160_упоение_несчастие_себятешение_действительн...   

                                        Representation  \
0    [тотчас, случай, входить, разумихин, мысль, ни...   
1    [раскольников, раскольник, юродивый, николай, ...   
2    [соня, сон, сонечка, спать, пойти, страшный, к...   
3    [одеваться, застегиваться, платье, надевать, п...   
4    [отворять, отпирать, отворяться, запираться, з...   
..                                                 ...   
157  [звякнуть, звонить, стучать, крикнуть, позвони...   
158  [благословлять, уведомлять, посвататься, испол...   
159  [выражение, противоречить, лесть, приторность,...   
160  [проговаривать, вздрагивать, свидригайлов, рас...   
161  [упоение, несчастие, себятешение, действительн...   

                                   Representative_Docs  
0    [слово      видеть        сей   пора       нич...  
1    [отвечать   раскольников, раскольников, раскол...  
2    [соня   замечать, соня   ничто     говорить, п...  
3    [хорошенький   летний   пиджак   светло   кори...  
4    [ключ    отворять     дверь       низкий   чел...  
..                                                 ...  
157  [незнакомец   звякнуть          подождать     ...  
158  [просьба   ваш      брат         наш   свидани...  
159  [лесть     весь     последний   нотка   фальши...  
160  [говорить   это    свидригайлов       чрезвыча...  
161  [заговаривать     целий          весь     болт...  

[162 rows x 5 columns]

## Рассмотрим три вида расстояний для UMAP

In [23]:
!pip install -U plotly==5.19.0
from bertopic import BERTopic
from nltk.corpus import stopwords
from umap import UMAP
from hdbscan import HDBSCAN
from bertopic import BERTopic
from sentence_transformers import SentenceTransformer
from sklearn.feature_extraction.text import CountVectorizer
from transformers.pipelines import pipeline
from bertopic.representation import KeyBERTInspired
from bertopic.vectorizers import ClassTfidfTransformer

from sentence_transformers import SentenceTransformer

import torch

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
embedding_model = SentenceTransformer('ai-forever/sbert_large_mt_nlu_ru')
umap_model = UMAP(n_components=5, metric='euclidean', n_neighbors=15, min_dist=0.0)
umap_model_mahalanobis = UMAP(n_components=5, metric='mahalanobis', n_neighbors=15, min_dist=0.0)
umap_model_manhattan = UMAP(n_components=5, metric='manhattan', n_neighbors=15, min_dist=0.0)
umap_model_chebyshev = UMAP(n_components=5, metric='chebyshev', n_neighbors=15, min_dist=0.0)
hdbscan_model = HDBSCAN(min_samples=10, gen_min_span_tree=True, prediction_data=True)
vectorizer_model = CountVectorizer(stop_words=stopwords.words('russian') + stopwords.words('english'))
ctfidf_model = ClassTfidfTransformer()
representation_model = KeyBERTInspired()
def create_topic_model_dist(docs, umap):
    return BERTopic(language="russian", embedding_model=embedding_model, umap_model=umap, hdbscan_model=hdbscan_model, vectorizer_model=vectorizer_model, ctfidf_model=ctfidf_model, representation_model=representation_model).fit(docs)


### Euclidean

In [6]:
euclidean_model = create_topic_model_dist(sentences['text'].to_list(), umap_model)
euclidean_model.get_topic_info()

Topic  Count                                           Name  \
0       -1   5266    -1_свидригайлов_ивановна_романовна_господин   
1        0    478     0_раскольников_раскольник_юродивый_николай   
2        1    297                 1_деньги_кошелек_платить_сумма   
3        2    166  2_беспамятство_ощущать_грезиться_задумчивость   
4        3    165                     3_соня_сонечка_спать_пойти   
..     ...    ...                                            ...   
136    135      5               135_шаг_идти_проходить_крепиться   
137    136      5         136_разумихин_зосимов_здоровый_великий   
138    137      5  137_привставать_государь_вскричать_приглашать   
139    138      5      138_побледнеть_чувство_романыч_воображать   
140    139      5                139_правда_факт_сплетня_низость   

                                        Representation  \
0    [свидригайлов, ивановна, романовна, господин, ...   
1    [раскольников, раскольник, юродивый, николай, ...   
2    [деньги, кошелек, платить, сумма, рубль, запла...   
3    [беспамятство, ощущать, грезиться, задумчивост...   
4    [соня, сонечка, спать, пойти, кукушка, страшны...   
..                                                 ...   
136  [шаг, идти, проходить, крепиться, мгновение, с...   
137  [разумихин, зосимов, здоровый, великий, беспок...   
138  [привставать, государь, вскричать, приглашать,...   
139  [побледнеть, чувство, романыч, воображать, мол...   
140  [правда, факт, сплетня, низость, правый, сумас...   

                                   Representative_Docs  
0    [господи        знать      убивать   лизавета ...  
1    [хотеть    отвечать   раскольников, отвечать  ...  
2    [вскрикивать          деньги      катерина   и...  
3    [минута     ужасно   похожий        ощущение  ...  
4    [соня   ничто     говорить, пойти          сон...  
..                                                 ...  
136  [шаг   стихать, идти     шаг   двести    трист...  
137  [разумихин     благоговение   смотреть     дун...  
138  [первый     свой   визит     объявлять        ...  
139  [сказать   это        смущаться     побледнеть...  
140  [это        сумасшедший     считать           ...  

[141 rows x 5 columns]

In [7]:
euclidean_model.visualize_barchart()

In [8]:
euclidean_model.visualize_topics()

In [9]:
euclidean_model.visualize_hierarchy()

In [10]:
euclidean_model.visualize_term_rank()

In [11]:
euclidean_model.visualize_heatmap()


### Chebyshev

In [12]:
cheb_model = create_topic_model_dist(sentences['text'].to_list(), umap_model_chebyshev)

In [13]:
cheb_model.get_topic_info()

Topic  Count                                        Name  \
0       -1   6318  -1_разумихин_свидригайлов_авдотья_ивановна   
1        0    537   0_раскольников_раскольник_батюшка_николай   
2        1    232  1_простоволосый_белокурый_красивый_румяный   
3        2    208                  2_соня_спаться_сонечка_сон   
4        3    110     3_схватывать_ударять_нагибаться_дернуть   
..     ...    ...                                         ...   
96      95      5       95_вскричать_помнить_прийти_вспомнить   
97      96      5    96_мост_столпиться_улица_останавливаться   
98      97      5      97_укорять_помириться_угрызение_любить   
99      98      5   98_оборачиваться_проходить_голос_шевелить   
100     99      5  99_разумихин_зосимов_раскольников_вахрушин   

                                        Representation  \
0    [разумихин, свидригайлов, авдотья, ивановна, р...   
1    [раскольников, раскольник, батюшка, николай, р...   
2    [простоволосый, белокурый, красивый, румяный, ...   
3    [соня, спаться, сонечка, сон, просыпаться, спа...   
4    [схватывать, ударять, нагибаться, дернуть, взв...   
..                                                 ...   
96   [вскричать, помнить, прийти, вспомнить, кликну...   
97   [мост, столпиться, улица, останавливаться, идт...   
98   [укорять, помириться, угрызение, любить, лизав...   
99   [оборачиваться, проходить, голос, шевелить, да...   
100  [разумихин, зосимов, раскольников, вахрушин, а...   

                                   Representative_Docs  
0    [почему            улыбаться    сказать   свид...  
1    [хотеть    отвечать   раскольников, раскольник...  
2    [соня     малый   рост    год   восемнадцать  ...  
3         [соня   замечать, пойти          соня, соня]  
4    [бросаться   стремглав     топор    это     то...  
..                                                 ...  
96   [научать          дмитрий   прокофьич         ...  
97   [канава      очень   далеко     мост       дох...  
98   [это     писать      любить   дуня    родя    ...  
99   [доходить   шаг   десять        узнавать      ...  
100  [разумихин     раскольник   приходиться   напр...  

[101 rows x 5 columns]

In [14]:
cheb_model.visualize_topics()

In [15]:
cheb_model.visualize_hierarchy()

In [16]:
cheb_model.visualize_term_rank()

In [17]:
cheb_model.visualize_barchart()

In [18]:
cheb_model.visualize_heatmap()

### Manhattan

In [24]:
manh_model = create_topic_model_dist(sentences['text'].to_list(), umap_model_manhattan)

In [25]:
manh_model.get_topic_info()

Topic  Count                                               Name  \
0       -1   5315           -1_ивановна_романовна_свидригайлов_софья   
1        0    478         0_раскольников_раскольник_юродивый_николай   
2        1    188                         1_соня_сонечка_спать_пойти   
3        2     96                  2_выговаривать_этакий_случай_этак   
4        3     89               3_смысл_принцип_помрачение_основание   
..     ...    ...                                                ...   
143    142      5                142_озноб_ощущать_спина_чувствовать   
144    143      5       143_отступать_разрывать_выбрасывать_выходить   
145    144      5         144_дрожать_проговаривать_ослабевать_голос   
146    145      5  145_побуждение_начинаться_предчувствовать_пере...   
147    146      5  146_свидригайлов_порфирий_тревожить_подозрител...   

                                        Representation  \
0    [ивановна, романовна, свидригайлов, софья, ска...   
1    [раскольников, раскольник, юродивый, николай, ...   
2    [соня, сонечка, спать, пойти, страшный, злой, ...   
3    [выговаривать, этакий, случай, этак, следовать...   
4    [смысл, принцип, помрачение, основание, солгат...   
..                                                 ...   
143  [озноб, ощущать, спина, чувствовать, холод, пр...   
144  [отступать, разрывать, выбрасывать, выходить, ...   
145  [дрожать, проговаривать, ослабевать, голос, го...   
146  [побуждение, начинаться, предчувствовать, пере...   
147  [свидригайлов, порфирий, тревожить, подозрител...   

                                   Representative_Docs  
0    [позволять    позволять        отчасти    весь...  
1    [самый   дело         подумать   раскольников,...  
2    [соня   замечать, соня   ничто     говорить, п...  
3    [например              тема    насчет   колоко...  
4    [именно   состоять          человек      закон...  
..                                                 ...  
143  [нога     неметь     подгибаться      идти, ле...  
144  [отступать, готовиться     драться            ...  
145  [голос     ослабевать, настасья          молча...  
146  [скрепляться   изо   весь   сила    приготовля...  
147  [особенно   тревожить     свидригайлов        ...  

[148 rows x 5 columns]

In [26]:
manh_model.visualize_topics()

In [27]:
manh_model.visualize_hierarchy()

In [28]:
manh_model.visualize_term_rank()

In [29]:
manh_model.visualize_barchart()

In [30]:
manh_model.visualize_heatmap()

### Mahalanobis

In [31]:
mah_model = create_topic_model_dist(sentences['text'].to_list(), umap_model_mahalanobis)

In [32]:
mah_model.get_topic_info()

Topic  Count                                               Name  \
0       -1   1457                -1_произносить_входить_ничто_случай   
1        0    100  0_митрофаниевский_принижение_затериваться_искр...   
2        1     69             1_михайловна_засыпать_растягиваться_ми   
3        2     57  2_приотворяться_способствовать_заискивать_знам...   
4        3     54      3_прерываться_обличение_оканчивать_прошептать   
..     ...    ...                                                ...   
391    390      6         390_рассчитать_спрашивать_время_отыскивать   
392    391      5             391_прочитывать_порфирий_кроткий_тихий   
393    392      5        392_горячиться_накидываться_завлекать_взять   
394    393      5                    393_прощай_мысль_озарять_любить   
395    394      5            394_вскричать_прочитывать_мочь_скривить   

                                        Representation  \
0    [произносить, входить, ничто, случай, тотчас, ...   
1    [митрофаниевский, принижение, затериваться, ис...   
2    [михайловна, засыпать, растягиваться, ми, влас...   
3    [приотворяться, способствовать, заискивать, зн...   
4    [прерываться, обличение, оканчивать, прошептат...   
..                                                 ...   
391  [рассчитать, спрашивать, время, отыскивать, бе...   
392  [прочитывать, порфирий, кроткий, тихий, соглас...   
393  [горячиться, накидываться, завлекать, взять, п...   
394  [прощай, мысль, озарять, любить, мгновение, ду...   
395  [вскричать, прочитывать, мочь, скривить, увере...   

                                   Representative_Docs  
0    [равный   образ          дуня     полслова    ...  
1    [объявлять        весь        единый    болтун...  
2    [слушать   внимательно      дворник      кох  ...  
3    [разговор   показываться     занимательный    ...  
4    [ваш   теория         верить            убегат...  
..                                                 ...  
391  [вообще     казаться        роковой   минута  ...  
392  [думать       вчера      вагон        это     ...  
393  [случаться          безнадежный, собственно   ...  
394  [мгновение       мысль   ярко   озарять      т...  
395  [широкий      сто   тысяча, уверенный    отвеч...  

[396 rows x 5 columns]

In [33]:
mah_model.visualize_topics()

In [34]:
mah_model.visualize_hierarchy()

In [35]:
mah_model.visualize_term_rank()

In [36]:
mah_model.visualize_barchart()

In [37]:
mah_model.visualize_heatmap()

## Выводы


Разбиение на предложения было выбрано для увеличения кол-во взодных данных модели, что гарантировало лучшую кластеризацию данных. Мы явно можем заметить, что модель выделяет в отдельные топики предложения о боге, деньгах, о сне и о Соне(прикольный момент), а также глаголы действий, имена, чувства и предмет декора или одежды

Расстояние манхэтенна очень хорошо выделяет именно глаголы, что можно заметить из графика бэрхэрта. Мне больше понравилась работа расстояния чебышева, оно быстро считается, лучше группирует топики и не запутывается в глаголах, но оставляет много неразмеченных данных. Расстояние Евклида работает чуть медленне и созздает много лишних тем. Расстояние махаланобиса, по-сути, должно сработать лучше всех, но оно у меня так и не досчиталось, очень тяжелый алгоритм(((((

МАХАЛАНОБИС ЗАГРУЗИЛСЯ. Хороший алгоритм, почти не оставил неразмеченных данных
Но они слабо сгруппированы
Можно попоробавать уменьшить его размерность


In [42]:
mah_model.reduce_topics(sentences['text'].to_list(), nr_topics=30)

In [43]:
mah_model.get_topic_info()

Topic  Count                                          Name  \
0      -1   1457                  -1_знать_узнавать_это_любить   
1       0   7530      0_сказать_проговаривать_говорить_входить   
2       1     39       1_упоение_понимающий_елагин_предстоящий   
3       2     37      2_направляться_кланяться_дверь_толковать   
4       3     29     3_ощущать_прикасаться_касаться_мерещиться   
5       4     29   4_срам_визжаливать_омерзение_сладострастный   
6       5     26         5_прощать_общество_захворать_замирать   
7       6     15    6_воротиться_раскольников_идти_поклоняться   
8       7     13        7_прочее_рассмеяться_получать_говорить   
9       8     13           8_забываться_бред_сделаться_ударять   
10      9     12      9_прочитывать_намерение_покраснеть_мысль   
11     10     11       10_изволить_пьяный_вскричать_оскорблять   
12     11     11   11_побледнеть_выражение_засмеяться_ивановна   
13     12     10              12_побледнеть_ничто_полнота_злой   
14     13      9  13_прощать_всевышний_рассердиться_милостивый   
15     14      9    14_романовна_скорбный_отчаянный_наружность   
16     15      8     15_отделывать_почернеть_отходить_выдирать   
17     16      8   16_воскрешать_ночевать_сказать_рассказывать   
18     17      7   17_вскричать_письмо_милостивый_свидригайлов   
19     18      7             18_кутья_вынимать_карман_маменька   
20     19      7   19_оборачиваться_проходить_являться_служить   
21     20      7     20_ивановна_который_нахмуриться_разумихин   
22     21      7       21_служба_прозывать_порфирий_обозначать   
23     22      6     22_рассчитать_спрашивать_время_отыскивать   
24     23      6      23_выговаривать_мочь_кривиться_вчерашний   
25     24      6          24_издыхание_прощать_ранить_убийство   
26     25      5    25_горячиться_накидываться_завлекать_взять   
27     26      5                26_прощай_мысль_озарять_любить   
28     27      5         27_прочитывать_порфирий_кроткий_тихий   
29     28      5        28_вскричать_прочитывать_мочь_скривить   

                                       Representation  \
0   [знать, узнавать, это, любить, сказать, спраши...   
1   [сказать, проговаривать, говорить, входить, го...   
2   [упоение, понимающий, елагин, предстоящий, кот...   
3   [направляться, кланяться, дверь, толковать, вы...   
4   [ощущать, прикасаться, касаться, мерещиться, в...   
5   [срам, визжаливать, омерзение, сладострастный,...   
6   [прощать, общество, захворать, замирать, никол...   
7   [воротиться, раскольников, идти, поклоняться, ...   
8   [прочее, рассмеяться, получать, говорить, прин...   
9   [забываться, бред, сделаться, ударять, отворят...   
10  [прочитывать, намерение, покраснеть, мысль, по...   
11  [изволить, пьяный, вскричать, оскорблять, поно...   
12  [побледнеть, выражение, засмеяться, ивановна, ...   
13  [побледнеть, ничто, полнота, злой, лужин, чист...   
14  [прощать, всевышний, рассердиться, милостивый,...   
15  [романовна, скорбный, отчаянный, наружность, а...   
16  [отделывать, почернеть, отходить, выдирать, ус...   
17  [воскрешать, ночевать, сказать, рассказывать, ...   
18  [вскричать, письмо, милостивый, свидригайлов, ...   
19  [кутья, вынимать, карман, маменька, салфетка, ...   
20  [оборачиваться, проходить, являться, служить, ...   
21  [ивановна, который, нахмуриться, разумихин, не...   
22  [служба, прозывать, порфирий, обозначать, шум,...   
23  [рассчитать, спрашивать, время, отыскивать, бе...   
24  [выговаривать, мочь, кривиться, вчерашний, сму...   
25  [издыхание, прощать, ранить, убийство, закрича...   
26  [горячиться, накидываться, завлекать, взять, п...   
27  [прощай, мысль, озарять, любить, мгновение, ду...   
28  [прочитывать, порфирий, кроткий, тихий, соглас...   
29  [вскричать, прочитывать, мочь, скривить, увере...   

                                  Representative_Docs  
0   [это, видеть      последний   время          з...  
1   [мочь      ваш   знать, думать      весь      ...  
2   [странный        

Теперь большинство глаголов относящихся к разговору улетело в 0 топик и видно остальные топики